# Python分析任务

在本章节中，我们会基于电表、电池、EnergyBase和EnergyWay的数据，完成日常数据分析和软件开发过程中经常会涉及到的分析工作，以更好地上手开发任务，提升数据分析的能力并拓宽数据分析的应用场景。

具体来说，关键的分析任务包括：
1. 站点需量情况
2. 电芯和设备温度情况
3. 电池衰减情况
4. 电池寿命预测
5. 软件工具使用

---

In [90]:
import os
import datetime
from glob import glob
from scipy.optimize import curve_fit

import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt

import warnings
warnings.filterwarnings('ignore')

# Make this notebook reproducible
np.random.seed(11)

## 分析站点的每日和每月需量情况
对于需量结算的客户，客户需要知道原负荷和储能运行后负荷的需量情况，用以评估需量节省的效果。我们可以基于EnergyWay电表的数据，来达到这个目的。

In [8]:
# 备用函数：不同时间精度的数据互相转换
def parse_data(data, input_column_names, output_column_names, fill_whole_year=False, output_resolution='1min'):
    # Make sure all variables have the right format
    data['datetime'] = pd.to_datetime(data['datetime'])
    data = data.drop_duplicates(subset=['datetime'], keep='first')
    data = data.sort_values(by=['datetime']).set_index(['datetime'])
    final_data = pd.DataFrame()

    # Parse data for the each of the input columns
    for i in range(len(input_column_names)):
        input_column_name = input_column_names[i]
        output_column_name = output_column_names[i]
        p = pd.Series(data[input_column_name])

        # Construct a continuous data range for differentiation
        idx = pd.date_range(p.first_valid_index().floor('1min'),
                            p.last_valid_index().floor('1min'),
                            freq='5s')
        # Interpolate original data based on the index
        new_p = p.reindex(p.index.union(idx)).interpolate('linear').reindex(idx)

        # Construct a new data range with the desired frequency for integration
        new_idx = pd.date_range(p.index[0].floor(output_resolution),
                                p.index[-1].floor(output_resolution),
                                freq=output_resolution)

        # Aggregate the continuous data based on the final index
        parsed_data = pd.DataFrame(new_p.reindex(new_p.index.union(new_idx)).interpolate('linear').reindex(new_idx).
                                   reset_index()).rename(columns={'index': 'datetime',
                                                                  input_column_name: output_column_name})

        # Extrapolate for the whole year
        if fill_whole_year is True:
            start_dt = datetime.datetime(parsed_data['datetime'][0].year, 1, 1, 0, 0)
            end_dt = datetime.datetime(parsed_data['datetime'][0].year, 12, 31, 23, 59)
            year_range = pd.date_range(start_dt, end_dt, freq=output_resolution)
            new_data = pd.merge(pd.DataFrame({'datetime': year_range}),
                                parsed_data, on='datetime',
                                how='outer')
            # Fill in empty values
            new_data[output_column_name] = new_data[output_column_name]\
                .fillna(new_data[output_column_name].groupby(new_data['datetime'].dt.time).transform('mean')) \
                .fillna(new_data[output_column_name].groupby(new_data['datetime'].dt.hour).transform('mean')) \
                .fillna(new_data[output_column_name].groupby(new_data['datetime'].dt.day).transform('mean'))
        else:
            new_data = pd.DataFrame()
            new_data['datetime'] = parsed_data['datetime']
            new_data[output_column_name] = parsed_data[output_column_name]
            # Fill in empty values
            new_data[output_column_name] = new_data[output_column_name]\
                .fillna(new_data[output_column_name].groupby(new_data['datetime'].dt.time).transform('mean')) \
                .fillna(new_data[output_column_name].groupby(new_data['datetime'].dt.hour).transform('mean')) \
                .fillna(new_data[output_column_name].groupby(new_data['datetime'].dt.day).transform('mean'))

        # Store results
        if 'datetime' not in final_data.columns:
            final_data['datetime'] = new_data['datetime']
            final_data[output_column_name] = new_data[output_column_name]
        else:
            final_data[output_column_name] = new_data[output_column_name]

    return final_data


In [11]:
poi_folder = "sample_data/data_chuangyuan/创园并网点数据"
poi_2_folder = "sample_data/data_chuangyuan/创园次总电表数据"

# 读取两个电表的数据
df = pd.DataFrame()
for date_dir in os.listdir(poi_folder):
    data = pd.read_csv(poi_folder + '/' + date_dir)
    df = df.append(data)
df["datetime"] = pd.to_datetime(df["time"])
df["poi_power"] = df["activep"]
df = df[["datetime", "poi_power"]].sort_values(by="datetime").reset_index(drop=True)

df_2 = pd.DataFrame()
for date_dir in os.listdir(poi_2_folder):
    data = pd.read_csv(poi_2_folder + '/' + date_dir)
    df_2 = df_2.append(data)
df_2["datetime"] = pd.to_datetime(df_2["time"])
df_2["poi_2_power"] = df_2["activep"]
df_2 = df_2[["datetime", "poi_2_power"]].sort_values(by="datetime").reset_index(drop=True)

# 将两个电表的数据合并，并计算光伏数据
df_3 = df.set_index('datetime').reindex(df_2.set_index('datetime').index, method='nearest').reset_index()
data = pd.merge(df_2, df_3, on='datetime')
data["pv"] = data["poi_2_power"] - data["poi_power"]

# 将原数据转化为15min精度的标准数据
data = parse_data(data=data[["datetime", "poi_power", "poi_2_power", "pv"]], 
                  input_column_names=["poi_power", "poi_2_power", "pv"], 
                  output_column_names=["poi_power", "poi_2_power", "pv"], 
                  fill_whole_year=False, output_resolution='15min')
data.head(5)

datetime  poi_power  poi_2_power        pv
0 2022-01-24 17:45:00   6.633075     4.943956 -1.689119
1 2022-01-24 18:00:00   9.353846     9.853846  0.500000
2 2022-01-24 18:15:00   7.469231     7.892308  0.423077
3 2022-01-24 18:30:00   8.300000     8.800000  0.500000
4 2022-01-24 18:45:00   8.123077     8.523077  0.400000

**A** 确保时间的格式正确，并输出每一行值的日期、时间、月、小时数

In [14]:
data["datetime"] = pd.to_datetime(data["datetime"])
data["date"] = data["datetime"].dt.date.astype("string")
data["month"] = data["datetime"].dt.month
data["time"] = data["datetime"].dt.time
data["hour"] = data["datetime"].dt.hour
data.head(5)

datetime  poi_power  poi_2_power        pv        date      time  \
0 2022-01-24 17:45:00   6.633075     4.943956 -1.689119  2022-01-24  17:45:00   
1 2022-01-24 18:00:00   9.353846     9.853846  0.500000  2022-01-24  18:00:00   
2 2022-01-24 18:15:00   7.469231     7.892308  0.423077  2022-01-24  18:15:00   
3 2022-01-24 18:30:00   8.300000     8.800000  0.500000  2022-01-24  18:30:00   
4 2022-01-24 18:45:00   8.123077     8.523077  0.400000  2022-01-24  18:45:00   

   hour  month  
0    17      1  
1    18      1  
2    18      1  
3    18      1  
4    18      1

**B** 计算负荷和光伏数据15分钟的滑动平均值

In [24]:
data["load_15min"] = data["poi_power"].rolling(15).mean()
data["net_load_15min"] = data["poi_2_power"].rolling(15).mean()
data["pv_15min"] = data["pv"].rolling(15).mean()

**C** 筛选出2月份后的数据作为有效数据，画出所有数据随时间的曲线图，并目测需量最大的日期

In [25]:
df = data.copy(deep=True)
df = df[df["month"] >= 2].reset_index(drop=True)
df["load"] = (df["poi_power"] + df["poi_2_power"]).clip(lower=0)

fig = go.Figure()
fig.add_trace(go.Scatter(x=df['datetime'], y=df['load_15min'], 
                         name='负荷_15min', line=dict(color='gray', width=2)))
fig.add_trace(go.Scatter(x=df['datetime'], y=df['net_load_15min'], 
                         name='净负荷_15min', line=dict(color='green', width=2)))
fig.add_trace(go.Scatter(x=df['datetime'], y=df['pv_15min'], 
                         name='光伏_15min', line=dict(color='orange', width=2)))
fig.update_layout(title="站点负荷曲线", template="simple_white")
fig.show()

**D** 分别得出每天原负荷、净负荷的最大值，并输出2月份和3月份的需量值

In [26]:
# Check daily summary
daily_summary = pd.DataFrame()
daily_summary['load_max'] = df.groupby('date')['load_15min'].max()
daily_summary['net_load_max'] = df.groupby('date')['net_load_15min'].max()
daily_summary

# Check monthly summary
monthly_summary = pd.DataFrame()
monthly_summary['load_max'] = df.groupby('month')['load_15min'].max()
monthly_summary['net_load_max'] = df.groupby('month')['net_load_15min'].max()
monthly_summary

load_max  net_load_max
month                          
2      171.823370    154.606960
3      141.948315    124.471209

## 分析电池包每日电芯的温度情况

**A** 读取某个pack某一天的数据，统计每个峰谷时段充放电的开始和结束时间

In [33]:
# 读取数据
pack = pd.read_csv("sample_data/eb_base1_pack1.csv")
bms = pd.read_csv("sample_data/eb_base1_pack1_bms1.csv")

# 转换时间
pack["datetime"] = pd.to_datetime("20220518" + " " + pack['time'], format= '%Y%m%d %H:%M:%S')
pack['hour'] = pd.to_datetime(pack['time'], format='%H:%M:%S').dt.hour
pack = pack.iloc[:-10] # Remove the last 10 rows of the next day

bms["datetime"] = pd.to_datetime("20220518" + " " + bms['time'], format= '%Y%m%d %H:%M:%S')
bms['hour'] = pd.to_datetime(bms['time'], format='%H:%M:%S').dt.hour
bms = bms.iloc[:-10] # Remove the last 10 rows of the next day

# 根据pack的状态，找到时间
index_dt = {}
index_dt["charge_first_start_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] <= 8)]['datetime'])[0]
index_dt["charge_first_end_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] <= 8)]['datetime'])[-1]
index_dt["discharge_first_start_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] <= 12)]['datetime'])[0]
index_dt["discharge_first_end_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] <= 12)]['datetime'])[-1]
index_dt["charge_second_start_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] >= 11)]['datetime'])[0]
index_dt["charge_second_end_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] <= 17)]['datetime'])[-1]
index_dt["discharge_second_start_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] >= 16)]['datetime'])[0]
index_dt["discharge_second_end_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] >= 16)]['datetime'])[-1]

{'charge_first_start_dt': Timestamp('2022-05-18 00:01:05'),
 'charge_first_end_dt': Timestamp('2022-05-18 02:08:27'),
 'discharge_first_start_dt': Timestamp('2022-05-18 07:56:37'),
 'discharge_first_end_dt': Timestamp('2022-05-18 10:59:59'),
 'charge_second_start_dt': Timestamp('2022-05-18 11:15:24'),
 'charge_second_end_dt': Timestamp('2022-05-18 16:30:10'),
 'discharge_second_start_dt': Timestamp('2022-05-18 16:45:24'),
 'discharge_second_end_dt': Timestamp('2022-05-18 21:24:22')}

**B** 找到**第一次（谷时）**充电开始和结束时，该pack的平均电芯温度、最高电芯温度

In [38]:
# 根据开始结束时间，找到对应的电芯温度指标
bms_metrics = {}
bms_metrics["cell_t_avg"] = {}
bms_metrics["cell_t_max"] = {}
bms_metrics["cell_t_avg"]["charge_first_start_dt"] = \
    bms.loc[bms["datetime"] == index_dt["charge_first_start_dt"], "Tave"].iloc[0]
bms_metrics["cell_t_avg"]["charge_first_end_dt"] = \
    bms.loc[bms["datetime"] == index_dt["charge_first_end_dt"], "Tave"].iloc[0]
bms_metrics["cell_t_avg"]["daily"] = np.mean(bms["Tave"])

bms_metrics["cell_t_max"]["charge_first_start_dt"] = \
    bms.loc[bms["datetime"] == index_dt["charge_first_start_dt"], "Tmax"].iloc[0]
bms_metrics["cell_t_max"]["charge_first_end_dt"] = \
    bms.loc[bms["datetime"] == index_dt["charge_first_end_dt"], "Tmax"].iloc[0]
bms_metrics["cell_t_max"]["daily"] = np.max(bms["Tmax"])

bms_metrics

{'cell_t_avg': {'charge_first_start_dt': 25.75,
  'charge_first_end_dt': 26.167,
  'daily': 27.852942408377807},
 'cell_t_max': {'charge_first_start_dt': 27.0,
  'charge_first_end_dt': 27.0,
  'daily': 36.0}}

**C** 将上述两个环节写成函数的形式供调用，以分析其他天数和其他packs的情况

In [46]:
def obtain_pack_metrics(eb_folder, project_name, pcs, date, pack_ID):
    # Read pack and bms data    
    pack = pd.read_csv(eb_folder + "base1_pack{}.csv".format(str(pack_ID)))
    pack["datetime"] = pd.to_datetime(date + " " + pack['time'], format= '%Y%m%d %H:%M:%S')
    pack['hour'] = pd.to_datetime(pack['time'], format='%H:%M:%S').dt.hour
    pack = pack.iloc[:-10] # Remove the last 10 rows of the next day
    
    bms = pd.read_csv(eb_folder + "base1_pack{}_bms1.csv".format(str(pack_ID)))
    bms["datetime"] = pd.to_datetime(date + " " + bms['time'], format= '%Y%m%d %H:%M:%S')
    bms['hour'] = pd.to_datetime(bms['time'], format='%H:%M:%S').dt.hour
    bms = bms.iloc[:-10] # Remove the last 10 rows of the next day

    try:
        # Identify timestamp indexes of various charging cycles
        index_dt = {}
        index_dt["charge_first_start_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] <= 8)]['datetime'])[0]
        index_dt["charge_first_end_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] <= 8)]['datetime'])[-1]
        index_dt["discharge_first_start_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] <= 12)]['datetime'])[0]
        index_dt["discharge_first_end_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] <= 12)]['datetime'])[-1]
        index_dt["charge_second_start_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] >= 11)]['datetime'])[0]
        index_dt["charge_second_end_dt"] = list(pack[(pack['Stat'] == 5) & (pack['hour'] <= 17)]['datetime'])[-1]
        index_dt["discharge_second_start_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] >= 16)]['datetime'])[0]
        index_dt["discharge_second_end_dt"] = list(pack[(pack['Stat'] == 4) & (pack['hour'] >= 16)]['datetime'])[-1]

        # Find relevant bms metrics with the specific timestamp indexes
        bms_metrics = {}
        bms_metrics["cell_t_avg"] = {}
        bms_metrics["cell_t_max"] = {}
        bms_metrics["cell_t_avg"]["charge_first_start_dt"] = \
            bms.loc[bms["datetime"] == index_dt["charge_first_start_dt"], "Tave"].iloc[0]
        bms_metrics["cell_t_avg"]["charge_first_end_dt"] = \
            bms.loc[bms["datetime"] == index_dt["charge_first_end_dt"], "Tave"].iloc[0]
        bms_metrics["cell_t_avg"]["daily"] = np.mean(bms["Tave"])

        bms_metrics["cell_t_max"]["charge_first_start_dt"] = \
            bms.loc[bms["datetime"] == index_dt["charge_first_start_dt"], "Tmax"].iloc[0]
        bms_metrics["cell_t_max"]["charge_first_end_dt"] = \
            bms.loc[bms["datetime"] == index_dt["charge_first_end_dt"], "Tmax"].iloc[0]
        bms_metrics["cell_t_max"]["daily"] = np.max(bms["Tmax"])
        
    except:
        bms_metrics = {}
        bms_metrics["cell_t_avg"] = {}
        bms_metrics["cell_t_max"] = {}
        bms_metrics["cell_t_avg"]["charge_first_start_dt"] = np.nan
        bms_metrics["cell_t_avg"]["charge_first_end_dt"] = np.nan
        bms_metrics["cell_t_avg"]["daily"] = np.nan
        bms_metrics["cell_t_max"]["charge_first_start_dt"] = np.nan
        bms_metrics["cell_t_max"]["charge_first_end_dt"] = np.nan
        bms_metrics["cell_t_max"]["daily"] = np.nan
    
    return index_dt, bms_metrics
    
obtain_pack_metrics(
    eb_folder='sample_data/data_tianchen/',
    project_name="Tianchen", 
    pcs="pcs1", 
    date="20220518", 
    pack_ID=1)


({'charge_first_start_dt': Timestamp('2022-05-18 00:01:05'),
  'charge_first_end_dt': Timestamp('2022-05-18 02:08:27'),
  'discharge_first_start_dt': Timestamp('2022-05-18 07:56:37'),
  'discharge_first_end_dt': Timestamp('2022-05-18 10:59:59'),
  'charge_second_start_dt': Timestamp('2022-05-18 11:15:24'),
  'charge_second_end_dt': Timestamp('2022-05-18 16:30:10'),
  'discharge_second_start_dt': Timestamp('2022-05-18 16:45:24'),
  'discharge_second_end_dt': Timestamp('2022-05-18 21:24:22')},
 {'cell_t_avg': {'charge_first_start_dt': 25.75,
   'charge_first_end_dt': 26.167,
   'daily': 27.852942408377807},
  'cell_t_max': {'charge_first_start_dt': 27.0,
   'charge_first_end_dt': 27.0,
   'daily': 36.0}})

**D** 画出某一天所有pack最高电芯和平均电芯温度的曲线

In [45]:
def obtain_daily_cell_temp_fig(eb_folder, project_name, pcs, date):
    fig = go.Figure()
    for bms in os.listdir(eb_folder):
        if "bms1" in bms:
            # Read bms data
            pack = pd.read_csv(eb_folder + bms)
            pack["datetime"] = pd.to_datetime(date + " " + pack['time'], format= '%Y%m%d %H:%M:%S')

            # Plot max cell temperature for each pack
            pack = pack.iloc[:-10, :]
            fig.add_trace(go.Scatter(x=pack['datetime'], y=pack['Tmax'], name="{}最高温度".format(bms), 
                                     marker=dict(color="green"), showlegend=True))
            fig.add_trace(go.Scatter(x=pack['datetime'], y=pack['Tave'], name="{}平均温度".format(bms), 
                                     marker=dict(color="gray"), showlegend=True))

    fig.update_layout(title="{}项目{}电芯温度数据（最高温度和平均温度）".format(project_name, date), 
                      template="simple_white")
    fig.update_yaxes(range = [10, 40])
    
    return fig

fig = obtain_daily_cell_temp_fig(
    eb_folder="sample_data/data_tianchen/", 
    project_name="Tianchen", 
    pcs="pcs1", 
    date="20220518")
fig.show()

## 分析实验室和站点电池衰减情况

**A** 读取实验室电池衰减文件，得出初始容量、当前容量和衰减率

In [98]:
# 读取实验室电池衰减数据
data = pd.read_excel("sample_data/data_battery.xlsx")

# 保留循环数、恒流充电容量(Ah)两列数据，更换名字
data = data.loc[:, ["循环", "恒流充电容量(Ah)"]]
data = data.rename(columns={"循环": "cycle_number",
                            "恒流充电容量(Ah)": "capacity_ah"})

# 检查数据完整性
print(data.describe(include='all'))
print(data.isnull().sum())

# 计算初始容量、当前容量和衰减率
initial_capacity = data["capacity_ah"].iloc[0]
current_capacity = data["capacity_ah"].iloc[-1]
total_cycle_number = data["cycle_number"].iloc[-1]
current_deg_percent = round(abs((current_capacity - initial_capacity) / initial_capacity * 100), 2)
print(initial_capacity, current_capacity, total_cycle_number, current_deg_percent)


       cycle_number  capacity_ah
count   3025.000000  3025.000000
mean    1516.000000    73.566182
std      873.386608     3.630586
min        4.000000     0.600000
25%      760.000000    71.265000
50%     1516.000000    73.141000
75%     2272.000000    75.915000
max     3028.000000    80.579000
cycle_number    0
capacity_ah     0
dtype: int64
80.579 69.319 3028 13.97


**B** 画出电池容量和循环数的图

In [99]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=data[["cycle_number", "capacity_ah"]].dropna()['cycle_number'].values,
                         y=data[["cycle_number", "capacity_ah"]].dropna()['capacity_ah'],
                         line = dict(color='green', width=2),
                         mode='lines+markers', name='实验室衰减'))
fig.update_layout(template='simple_white', 
                  xaxis_title='循环（次)', xaxis_range=[0, 5000],
                  yaxis_title='容量 (Ah)', yaxis_range=[0,100], showlegend=True)
fig.show()

**C** 读取实际项目站点的充放电量数据，并画出充放电量随循环次数的曲线图

In [80]:
# 读取汉森项目数据
project_data = pd.read_csv("sample_data/data_hansen.csv")

# 计算每天充放电电量的总量
project_data["charge_kwh"] = project_data["valley_chg"] + project_data["flat_chg"] 
project_data["discharge_kwh"] = project_data["peak_dhg"] + project_data["peak2_dhg"]

# 计算充放电的等效等效容量
project_data["capacity_kwh"] = np.sqrt(project_data["charge_kwh"] * project_data["discharge_kwh"])

# 观察前7天的数据
project_data.head(7)

date  cycle_number  valley_chg  peak_dhg  flat_chg  peak2_dhg  \
0  1/1/20             0         229       195       229          0   
1  1/2/20             2           2       193       229        200   
2  1/3/20             4         231       197       229        198   
3  1/4/20             6         229       196       654          0   
4  1/7/20             8         231       197       135        199   
5  1/8/20            10         231       197       228        199   
6  1/9/20            12         231       195       180          0   

   charge_kwh  discharge_kwh  capacity_kwh  
0         458            195    298.847787  
1         231            393    301.302174  
2         460            395    426.262830  
3         883            196    416.014423  
4         366            396    380.704610  
5         459            396    426.337894  
6         411            195    283.098923

In [86]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=project_data["cycle_number"],
                         y=project_data["capacity_kwh"],
                         line = dict(color='orange', width=2),
                         mode='lines+markers', name='汉森项目衰减'))
fig.update_layout(template='simple_white', 
                  xaxis_title='循环（次)', xaxis_range=[0, 2000],
                  yaxis_title='等效容量 (kWh)', yaxis_range=[0,500], showlegend=True)
fig.show()

## 预测实验室电池衰减寿命

**A** 基于拟合公式对循环数据进行回归

In [114]:
# 给定拟合公式
def func_exp_1(X, c0, c1, c2, c3, tau):
    return c0 - c1 * ((X * 1) ** 0.5) - c2 * X - c3 * (1 - np.exp(-(X*1)/tau))

# 设置参数的上下限
param_bounds_1 = ([0, 0.1, 0.0004, 2.0, 0.01],
                  [np.inf, np.inf, np.inf, np.inf, np.inf])

# 进行拟合
popt_exp_1, pcov_exp_1 = curve_fit(
    func_exp_1, 
    data['cycle_number'].values, 
    data['capacity_ah'].values,
    bounds=param_bounds_1)

# 输出拟合结果
print(popt_exp_1)


[1.25759637e+03 2.00626620e-01 4.06961496e-04 1.17604437e+03
 1.06851489e-01]


**B** 预测10000次循环的寿命，对比预测结果和实际结果

In [115]:
# 进行寿命的预测
cycle_list = np.arange(1, 10000)
results = func_exp_1(cycle_list, *popt_exp_1)

# 在衰减曲线上增加预测结果
fig = go.Figure()
fig.add_trace(go.Scatter(x=data[["cycle_number", "capacity_ah"]].dropna()['cycle_number'].values,
                         y=data[["cycle_number", "capacity_ah"]].dropna()['capacity_ah'],
                         line = dict(color='green', width=2),
                         mode='lines+markers', name='实验室衰减'))
fig.add_trace(go.Scatter(x=cycle_list,
                         y=results,
                         line = dict(color='red', width=2),
                         mode='lines', name='预测结果'))
fig.update_layout(template='simple_white', 
                  xaxis_title='循环（次)', xaxis_range=[0, 5000],
                  yaxis_title='容量 (Ah)', yaxis_range=[0,100], showlegend=True)
fig.show()

**C** 考虑是否还有其他的拟合公式、或拟合方法？

参见：https://towardsdatascience.com/introduction-to-regression-analysis-9151d8ac14b3

In [122]:
import numpy as np
import seaborn as sns 
import pandas as pd
from pandas.plotting import scatter_matrix
import matplotlib.pyplot as plt 

from scipy import stats
from scipy.stats import norm

from sklearn.datasets import fetch_california_housing
from sklearn.metrics import r2_score, mean_squared_error
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression

# Read datasets
fetch_california_housing = fetch_california_housing()

pd = pd.DataFrame(fetch_california_housing.data, columns=fetch_california_housing.feature_names)
pd['AveHouseVal'] = (fetch_california_housing.target)*100000
pd

MedInc  HouseAge  AveRooms  AveBedrms  Population  AveOccup  Latitude  \
0      8.3252      41.0  6.984127   1.023810       322.0  2.555556     37.88   
1      8.3014      21.0  6.238137   0.971880      2401.0  2.109842     37.86   
2      7.2574      52.0  8.288136   1.073446       496.0  2.802260     37.85   
3      5.6431      52.0  5.817352   1.073059       558.0  2.547945     37.85   
4      3.8462      52.0  6.281853   1.081081       565.0  2.181467     37.85   
...       ...       ...       ...        ...         ...       ...       ...   
20635  1.5603      25.0  5.045455   1.133333       845.0  2.560606     39.48   
20636  2.5568      18.0  6.114035   1.315789       356.0  3.122807     39.49   
20637  1.7000      17.0  5.205543   1.120092      1007.0  2.325635     39.43   
20638  1.8672      18.0  5.329513   1.171920       741.0  2.123209     39.43   
20639  2.3886      16.0  5.254717   1.162264      1387.0  2.616981     39.37   

       Longitude  AveHouseVal  
0        -122.23     452600.0  
1        -122.22     358500.0  
2        -122.24     352100.0  
3        -122.25     341300.0  
4        -122.25     342200.0  
...          ...          ...  
20635    -121.09      78100.0  
20636    -121.21      77100.0  
20637    -121.22      92300.0  
20638    -121.32      84700.0  
20639    -121.24      89400.0  

[20640 rows x 9 columns]

In [123]:
# Choose features and variables
X = pd[['MedInc', 'Latitude', 'AveRooms']]
Y = pd['AveHouseVal']

X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size = 0.2, random_state=5)
lin_model = LinearRegression()
lin_model.fit(X_train, Y_train)

X_train, X_test, Y_train, Y_test = train_test_split(data[["cycle_number", "capacity_ah"]], data["capacity_ah"], 
                                                    test_size = 0.2, random_state=5)
lin_model = LinearRegression()
lin_model.fit(X_train, Y_train)

# model evaluation for training set
y_train_predict = lin_model.predict(X_train)
rmse = (np.sqrt(mean_squared_error(Y_train, y_train_predict)))
r2 = r2_score(Y_train, y_train_predict)

print("The model performance for training set")
print("--------------------------------------")
print('RMSE is {}'.format(rmse))
print('R2 score is {}'.format(r2))
print("\n")

# model evaluation for testing set
y_test_predict = lin_model.predict(X_test)
rmse = (np.sqrt(mean_squared_error(Y_test, y_test_predict)))
r2 = r2_score(Y_test, y_test_predict)

print("The model performance for testing set")
print("--------------------------------------")
print('RMSE is {}'.format(rmse))
print('R2 score is {}'.format(r2))

The model performance for training set
--------------------------------------
RMSE is 1.444383507343868e-16
R2 score is 1.0


The model performance for testing set
--------------------------------------
RMSE is 7.226570789156326e-16
R2 score is 1.0


## 软件使用工具

**1. Jupyter Notebook (https://jupyter.org/)**

Jupyter Notebook是一个开源 Web 应用程序，支持数据科学家、数据工程师、数学家、研究人员和其他用户之间的交互式协作。它是一个计算笔记本工具，可用于创建、编辑和共享代码，以及解释性文本、图像和其他信息。例如，Jupyter 用户可以将软件代码、计算、评论、数据可视化和计算结果的富媒体表示添加到单个文档（称为笔记本）中，然后可以与同事共享和修改。

因此，根据 Jupyter Notebook 的文档，笔记本“可以作为数据科学团队成员之间交互会话的完整计算记录”。笔记本文档是具有版本控制功能的 JSON 文件。此外，Notebook Viewer 服务使它们能够呈现为静态网页，以供系统上未安装 Jupyter 的用户查看。

Jupyter Notebook 起源于 Python 编程语言——它最初是 IPython 交互式工具包开源项目的一部分，在 2014 年被拆分出来。Julia、Python 和 R 的松散组合使 Jupyter 得名；除了支持这三种语言之外，Jupyter 还为其他数十种语言提供了模块化内核。

**2. Streamlit (https://streamlit.io/)**

Streamlit 是第一个专门针对机器学习和数据科学团队的应用开发框架，它是开发自定义机器学习工具的最快的方法，你可以认为它的目标是取代Flask在机器学习项目中的地位，可以帮助机器学习工程师快速开发用户交互工具。

Streamlit 基于tornado框架，封装了大量互动组件，同时也支持大量表格、图表、数据表等对象的渲染，并且支持栅格化响应式布局。

Streamlit的默认渲染语言就是markdown；除此以外，Streamlit也支持html文本的渲染，这意味着你也可以将任何html代码嵌入到streamlit应用里.

做网站采用的技术组合方案：

    1. 网站前后端都用js：vue + node.js等
    
    2. 网站前端用 html、css、javascript，网站后端用python：Flask、Django等
    
    3. 网站前后端都用Python：streamlit

**3. NumPy (https://numpy.org/)**

NumPy 是 Numerical Python 的缩写，是一个开源 Python 库，广泛用于科学计算、工程、数据科学和机器学习应用程序。该库由多维数组对象和用于处理这些数组以启用各种数学和逻辑功能的例程组成。它还支持线性代数、随机数生成等运算。

NumPy 的核心组件之一是 N 维数组或 ndarray，它表示相同类型和大小的项目的集合。关联的数据类型对象描述了数组中数据元素的格式。相同的数据可以由多个 ndarray 共享，并且可以在另一个中查看在一个中所做的数据更改。

NumPy 是在 2006 年通过组合和修改两个早期库的元素而创建的。 NumPy 网站将其吹捧为“在 Python 中处理数值数据的通用标准”，并且由于其众多内置函数，它通常被认为是 Python 最有用的库之一。它还以其速度而闻名，部分原因在于其核心使用了优化的 C 代码。此外，各种其他 Python 库都建立在 NumPy 之上。

**4. Pandas (https://pandas.pydata.org/)**

另一个流行的开源 Python 库，pandas 通常用于数据分析和操作。它建立在 NumPy 之上，具有两个主要的数据结构：Series 一维数组和 DataFrame，这是一种用于集成索引的数据操作的二维结构。两者都可以接受来自 NumPy ndarrays 和其他输入的数据；一个 DataFrame 也可以包含多个 Series 对象。

Pandas 创建于 2008 年，具有内置的数据可视化功能、探索性数据分析功能，并支持包括 CSV、SQL、HTML 和 JSON 在内的文件格式和语言。此外，据熊猫网站介绍，它还提供智能数据对齐、缺失数据的集成处理、数据集的灵活重塑和旋转、数据聚合和转换以及快速合并和加入数据集的能力等功能。

Pandas 的开发人员表示，他们的目标是使其成为“在 Python 中进行实用的、真实的数据分析的基本高级构建块”。 Pandas 中的关键代码路径是用 C 或 Python 的 Cython 超集编写的，以优化其性能，并且该库可用于各种分析和统计数据，包括表格、时间序列和标记矩阵数据集。

**5. Scikit-learn (https://scikit-learn.org/)**

Scikit-learn 是一个用于 Python 的开源机器学习库，它建立在 SciPy 和 NumPy 科学计算库以及用于绘制数据的 Matplotlib 之上。它支持有监督和无监督的机器学习，并包含许多算法和模型，在 scikit-learn 中称为估计器。此外，它还提供模型拟合、选择和评估以及数据预处理和转换的功能。

该库最初名为 scikits.learn，于 2007 年作为 Google Summer of Code 项目开始，并于 2010 年首次公开发布。其名称的第一部分是 SciPy 工具包的缩写，也被其他 SciPy 附加组件使用包。 Scikit-learn 主要处理存储在 NumPy 数组或 SciPy 稀疏矩阵中的数值数据。

该库的工具套件还支持各种其他任务，例如数据集加载和创建结合数据转换器对象和估计器的工作流。但是由于设计限制，scikit-learn 有一些限制。例如，它不支持深度学习、强化学习或 GPU，图书馆的网站称其开发人员“只考虑包含完善的算法”。

**6. SciPy (https://scipy.org/)**

SciPy 是另一个支持科学计算用途的开源 Python 库。 Scientific Python 的缩写，它具有一组数学算法以及用于数据操作和可视化的高级命令和类。它包括十几个子包，其中包含用于数据优化、积分和插值等功能的算法和实用程序，以及代数方程、微分方程、图像处理和统计。

SciPy 库建立在 NumPy 之上，可以在 NumPy 数组上运行。但是 SciPy 提供了额外的数组计算工具并提供了专门的数据结构，包括稀疏矩阵和 k 维树，以扩展 NumPy 的能力。

SciPy 实际上早于 NumPy：它是在 2001 年创建的，它结合了为作为 NumPy 的前身之一的 Numeric 库构建的不同附加模块。与 NumPy 一样，SciPy 使用编译后的代码来优化性能；在这种情况下，该库的大部分性能关键部分都是用 C、C++ 或 Fortran 编写的。